In [2]:
!pip install pandas spacy tensorflow imbalanced-learn

In [3]:
!python -m spacy download en_core_web_sm

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 42.2 MB/s eta 0:00:00
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_sm')
⚠ Restart to reload dependencies
If you are in a Jupyter or Colab notebook, you may need to restart Python in
order to load all the package's dependencies. You can do this by selecting the
'Restart kernel' or 'Restart runtime' option.


In [ ]:
#import libraries
import pandas as pd
import spacy
from tensorflow.keras.preprocessing.text import one_hot
from tensorflow.keras.preprocessing.sequence import pad_sequences
import numpy as np
from imblearn.over_sampling import SMOTE
from sklearn.model_selection import train_test_split
import tensorflow as tf
from tensorflow import keras
from sklearn.metrics import classification_report, confusion_matrix
import seaborn as sns

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
df = pd.read_csv('/content/drive/MyDrive/Capstone Material/Datasets/pre_pro1.csv')
df

In [ ]:
#check null values
df.isna().sum()

sentence    1
labels      0
dtype: int64

In [ ]:
def safe_lower(val):
    if isinstance(val, str):
        return val.lower()
    return val

In [ ]:
df['sentence'].apply(safe_lower)

0        rt dinerolocobo if nigga fuck bitch dat ha cat...
1                   rt dinofool ima catfish bitch fake arm
2        rt dinofool yall ever normal day mind play hor...
3        rt diponlin i close eye shit sometim bitch abl...
4        rt diponlin if k michel apart baltimor twitter...
                               ...                        
21078                            i think there water kadir
21079    even though bangladesh bangladesh jamaateislam...
21080                                     rais gelig salsa
21081                                   i want fuck lawyer
21082                           thi whore tarek night meal
Name: sentence, Length: 21083, dtype: object

In [ ]:
import re
def remove_html_tags(text):
    if isinstance(text, str):
        pattern = re.compile('<.*?>')
        return pattern.sub(r'', text)
    return text

In [ ]:
df['sentence'] = df['sentence'].apply(remove_html_tags)

In [ ]:
def romove_url(text):
  pattern = re.compile(r'https?://\S+|www\.\S+')
  return pattern.sub(r'', text)

In [ ]:
df['sentence'].apply(romove_url)

TypeError: expected string or bytes-like object

In [ ]:
chat_words={
'afaik': 'as far as i know',
'afk': 'away from keyboard',
'asap': 'as soon as possible',
'atk': 'at the keyboard',
'atm': 'at the moment',
'a3': 'anytime anywhere anyplace',
'bak': 'back at keyboard',
'bbl': 'be back later',
'bbs': 'be back soon',
'bfn': 'bye for now',
'b4n': 'bye for now',
'brb': 'be right back',
'brt': 'be right there',
'btw': 'by the way',
'b4': 'before',
'cu': 'see you',
'cul8r': 'see you later',
'cya': 'see you',
'faq': 'frequently asked questions',
'fc': 'fingers crossed',
'fwiw': 'for what it is worth',
'fyi': 'for your information',
'gal': 'get a life',
'gg': 'good game',
'gn': 'good night',
'gmta': 'great minds think alike',
'gr8': 'great!',
'g9': 'genius',
'ic': 'i see',
'icq': 'i seek you also a chat program',
'ilu': 'i love you',
'imho': 'in my honest humble opinion',
'imo': 'in my opinion',
'iow': 'in other words',
'irl': 'in real life',
'kiss': 'keep it simple, stupid',
'ldr': 'long distance relationship',
'lmao': 'laugh my a.. off',
'lol': 'laughing out loud',
'ltns': 'long time no see',
'l8r': 'later',
'mte': 'my thoughts exactly',
'm8': 'mate',
'nrn': 'no reply necessary',
'oic': 'oh i see',
'pita': 'pain in the a..',
'prt': 'party',
'prw': 'parents are watching',
'qpsa': 'que pasa',
'rofl': 'rolling on the floor laughing',
'roflol': 'rolling on the floor laughing out loud',
'rotflmao': 'rolling on the floor laughing my a.. off',
'sk8': 'skate',
'stats': 'your sex and age',
'asl': 'age, sex, location',
'thx': 'thank you',
'ttfn': 'ta-ta for now!',
'ttyl': 'talk to you later',
'u': 'you',
'u2': 'you too',
'u4e': 'yours for ever',
'wb': 'welcome back',
'wtf': 'what the fuck',
'wtg': 'way to go!',
'wuf': 'where are you from?',
'w8': 'wait',
'7k': 'sick:-d laugher',
'tfw': 'that feeling when. tfw internet slang often goes in a caption to an image.',
'mfw': 'my face when',
'mrw': 'my reaction when',
'ifyp': 'i feel your pain',
'lol': 'laughing out loud',
'tntl': 'trying not to laugh',
'jk': 'just kidding',
'idc': 'i don’t care',
'ily': 'i love you',
'imu': 'i miss you',
'adih': 'another day in hell',
'idc': 'i don’t care',
'zzz': 'sleeping, bored, tired',
'wywh': 'wish you were here',
'time': 'tears in my eyes',
'bae': 'before anyone else',
'fimh': 'forever in my heart',
'bsaaw': 'big smile and a wink',
'bwl': 'bursting with laughter',
'lmao': 'laughing my ass off',
'bff': 'best friends forever',
'csl': 'can not stop laughing',
}

In [ ]:
def chat_conversion(text):
  new_text = []
  for w in text.split():
    if w.upper() in chat_words:
      new_text.append(chat_words[w.upper()])
    elif w.lower() in chat_words:
       new_text.append(chat_words[w.lower()])
    else:
      new_text.append(w)
  return " ".join(new_text)

In [ ]:
df['sentence'] = df['sentence'].apply(chat_conversion)

In [ ]:
pip install emoji --upgrade

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 431.4/431.4 kB 15.7 MB/s eta 0:00:00


In [ ]:
import emoji
print(emoji.demojize('python is 😀'))


python is :grinning_face:


In [ ]:
for i in range(11005):
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
  print(emoji.demojize(df['sentence'][i]))

<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2:

RT @DineroLoco_Bo: If a nigga fuck my bitch dats on ha cat .. but ima leave yu alone fa being trifling
RT @Dino_FooL: Ima catfish a bitch with fake arms
RT @Dino_FooL: Y'all ever just been having a normal day and your mind plays a horrible trick on you and give you a whiff of some good pussy&#8230;
RT @DipOnline I be closing my eyes and shit sometimes so bitches be able to sneak a quick nipple lick in.. But she ain't going ham on me yo
RT @DipOnline If K Michelle was apart of Baltimore twitter she'd be one of them hoes saying she's celibate smh
RT @Dipset_Kenn: RT @ToneThaMan55: RT @PAPER_CHAYSIN: I love money fuc a bitch I won't stress myself , and I keep my mouth closed cuz I can&#8230;
RT @Dirrttyydan: Chi ain't no bitch then you got them Assyrian kings on California and Peterson &#128081;&#128081;
RT @DirtyEaffiliate: you can't turn a hoe into a housewife hashtag tupac
RT @DivaMonRoe2uHoE: Fuck candy. Eat pussy. &#128527;
RT @DivaMonRoe2uHoE: Niggas always wanna talk about how God 

<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2:

RT @EchelonInsights: Rick Scott beating win number in 30 counties, Charlie Crist in 13. #FLGOV
RT @EinsteinParody: Waterproof lab coat in case I drown in the pussy #swag
RT @EisenbackEmily: I hate when people leave their trash in my car.
RT @ElJefeDeJefes4C: "@Virgilio_LLA: Jammin these sad songs, smoking squares thinking bout bitches..." lmfao
RT @El_Grillo1: In the ME, the crow would eat the bear MT @webradius Obviously not in the ME MT @solemnwatch: Bear Saves Drowning Crow - An&#8230;
RT @ElderLWM: And Black women need to stop referring to themselves and other sisters as "hoes" &amp; "Bitches"..... It really ain't a good look&#8230;
RT @EliRipRashad: I love them stripper bitches
RT @Elisaa_Martinez: Happy birthday cotton picker laughing out loud @1NOnlyDirtyMike
RT @Elisha40hands: bitch you got too many teeth in your mouth
RT @ElleHueyXIV: "Fuck me or I'll make you feel bad about it. But if you fuck other guys, I'll call you a hoe. And if you fuck me, I'll thi&#8230;
RT @Em_99car: 

<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2:

...

<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2:

Shobjai Salah Bourbon.
Oh, my God, destroy these atheist dogs.
The fatwa is a drug addict of the Islamic Lebasshadi Digital Hypocrisy, who is a drug addict with a shoe should be beaten to death in Bogopgogo, a fatwa that warns against the Islamic Lebashary Digital hypocrites in Bangladesh.
Why don't you tell me that you're a fucking hypocrisy without saying that he's born all right, Hafizur Rahman is right about you to get him to take you for his shoe.
This bitch is a fucking atheist.
If there is no Hedawat, give him more debt than Pharaoh's.
Punta Mugire
The atheist Kutarful
If Crazy Lang is you and you're a fucking crummy, and you're an idiot and you're a fucking idiot and you're an old man. I'm going to kill you both in front of you.
Why don't you burn this Salida?
The Bond. You are.
The violence of the People of the Book has increased, as many of the bravest men online. Why don't you just sit down directly?
Given the name of a bouncing, and I'm telling you, brother, you're better o

<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2:

If you beat the layout, you'll be right to beat it.
Let the file go for the Yaba season, the police.
We'll be there with good hands and we'll be there.
Gaza Hiroine cocktail.
May God destroy them if you don't guide them.
You're not getting company, you son of a bitch.
Donbugs must have been dreaming of them.
How do you feel about it?
The U.S. governor-in-law-in-law Shuni sire.
Heh-in-law sat by this.
You're an asshole.
I'm going to go to Gaza-I beg you.
Even if they're dead, sir's brother's brother is also going to give him some kind of shit.
In this world we can argue not in the next world, but in God you are the one who guides you all.
These frauds have made the name of Islam worse.
Oh, hell.
Brother I'm on the pass
The copy of the tahsinciation.
You're a fraud.
You see the devil's face, you don't live.
All of you?
Oh, my God, are you a cop?
What harm did he do?
Dad eats Gaza in Mirpur
It's all money for the infidels.
It's not fair at all Onny Bonde.
It's great to forget my father's 

<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentence'][i] = emoji.demojize(df['sentence'][i])
<ipython-input-21-cfdc2d635e40>:2:

In [ ]:
import string,time
string.punctuation

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'

In [ ]:
exclude = string.punctuation

In [ ]:
def remove_punc1(text):
  return text.translate(str.maketrans('','', exclude))

In [ ]:
df['sentence'] = df['sentence'].apply(remove_punc1)

In [ ]:
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


In [ ]:
def remove_stopwords(text):
  new_text = []

  for word in text.split():
    if word in stopwords.words('english'):
      new_text.append('')
    else:
      new_text.append(word)
  x = new_text[:]
  new_text.clear()
  return " ".join(x)

In [ ]:
df['sentence']=df['sentence'].apply(remove_stopwords)

In [ ]:
import spacy
nlp = spacy.load('en_core_web_sm')

In [ ]:
def process_text(text):
    doc = nlp(text)
    # You can perform any analysis here, for example, extracting named entities
    entities = [(ent.text, ent.label_) for ent in doc.ents]
    return entities

In [ ]:
df['sentence'].apply(process_text)

0                                                       []
1                                                       []
2                             [(RT DinoFooL Yall, PERSON)]
3                                                       []
4        [(RT DipOnline, ORG), (Michelle, PERSON), (Bal...
                               ...                        
21078                                                   []
21079    [(Bangladeshs Bangladesh JamaateIslami, PERSON...
21080                                       [(Salsa, GPE)]
21081                                                   []
21082                                   [(Tareks, PERSON)]
Name: sentence, Length: 21083, dtype: object

In [ ]:
import nltk
nltk.download('punkt')
from nltk.stem.porter import PorterStemmer

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


In [ ]:
ps = PorterStemmer()

In [ ]:
def stem_words(text):
    if isinstance(text, str):
        return " ".join([ps.stem(word) for word in text.split()])
    else:
        return text

In [ ]:
df['sentence'] = df['sentence'].apply(stem_words)

In [ ]:
df

sentence  labels
0      rt dinerolocobo if nigga fuck bitch dat ha cat...       1
1                 rt dinofool ima catfish bitch fake arm       1
2      rt dinofool yall ever normal day mind play hor...       1
3      rt diponlin i close eye shit sometim bitch abl...       1
4      rt diponlin if k michel apart baltimor twitter...       1
...                                                  ...     ...
21078                          i think there water kadir       1
21079  even though bangladesh bangladesh jamaateislam...       1
21080                                   rais gelig salsa       1
21081                                 i want fuck lawyer       1
21082                         thi whore tarek night meal       1

[21083 rows x 2 columns]

one-hot representation

In [ ]:
vocab_size = 10000
one_hot_representation = [one_hot(str(words), vocab_size) for words in df['sentence']]

In [ ]:
for i in range(0, 4):
  print(df['sentence'].iloc[i])

rt dinerolocobo if nigga fuck bitch dat ha cat ima leav yu alon fa trifl
rt dinofool ima catfish bitch fake arm
rt dinofool yall ever normal day mind play horribl trick give whiff good pussy8230
rt diponlin i close eye shit sometim bitch abl sneak quick nippl lick but aint go ham yo


In [ ]:
for i in range(0, 4):
  print(one_hot_representation[i])

[7317, 4909, 4223, 6306, 2695, 4304, 3745, 8940, 5435, 4411, 1974, 9136, 3006, 7229, 9965]
[7317, 2873, 4411, 6440, 4304, 8380, 7936]
[7317, 2873, 6505, 8635, 2486, 3782, 5501, 8054, 7234, 3967, 9384, 1878, 3906, 5703]
[7317, 2437, 8742, 1525, 7481, 3608, 3672, 4304, 5889, 2596, 1980, 7818, 3338, 9590, 3931, 3915, 1347, 2450]


In [ ]:
sentence_length = 20
embedded_tweet = pad_sequences(one_hot_representation, padding = 'pre' , maxlen = sentence_length )

In [ ]:
for i in range(0, 4):
  print(embedded_tweet[i])

[   0    0    0    0    0 7317 4909 4223 6306 2695 4304 3745 8940 5435
 4411 1974 9136 3006 7229 9965]
[   0    0    0    0    0    0    0    0    0    0    0    0    0 7317
 2873 4411 6440 4304 8380 7936]
[   0    0    0    0    0    0 7317 2873 6505 8635 2486 3782 5501 8054
 7234 3967 9384 1878 3906 5703]
[   0    0 7317 2437 8742 1525 7481 3608 3672 4304 5889 2596 1980 7818
 3338 9590 3931 3915 1347 2450]


In [ ]:
x = np.array(embedded_tweet)
y = np.array(df['labels'])

In [ ]:
df['labels'].value_counts()

labels
0    10617
1    10466
Name: count, dtype: int64

In [ ]:
smote = SMOTE(sampling_strategy='minority')
x, y = smote.fit_resample(x, y)

df['labels'].value_counts()

labels
0    10617
1    10466
Name: count, dtype: int64